###
Remember to upload the data to the folder before running the program
###

In [1]:
!pip install langdetect

     |████████████████████████████████| 983kB 9.7MB/s 
  Created wheel for langdetect: filename=langdetect-1.0.8-cp37-none-any.whl size=993193 sha256=c6ecb977d79db55a81f1a68c9a4e3a80fecdbc65a6b40628d318fd17d92ed6e4
  Stored in directory: /root/.cache/pip/wheels/8d/b3/aa/6d99de9f3841d7d3d40a60ea06e6d669e8e5012e6c8b947a57
Successfully built langdetect


In [ ]:
import itertools
import numpy as np
import os
import re
import string
import tensorflow as tf
import tqdm
from langdetect import detect
import pandas as pd

from tensorflow.keras.layers.experimental.preprocessing import TextVectorization
from tensorflow.keras import Model, Sequential
from tensorflow.keras.layers import Activation, Dense, Dot, Embedding, Flatten, GlobalAveragePooling1D, Reshape

SEED = 42 
AUTOTUNE = tf.data.AUTOTUNE

def custom_standardization(input_data):
  lowercase = tf.strings.lower(input_data)
  return tf.strings.regex_replace(lowercase,
                                  '[%s]' % re.escape(string.punctuation), '')

europe_csv = pd.read_csv('/european_tweets.csv')
english_tweets = []
for content in europe_csv["Text"]:
    if detect(content) == 'en':
        english_tweets.append(content.encode('utf-8'))

tweet_ds = tf.data.Dataset.from_tensor_slices(english_tweets)

# Define the vocabulary size and number of words in a sequence.
vocab_size = 10000
sequence_length = 75

# Use the text vectorization layer to normalize, split, and map strings to
# integers. Set output_sequence_length length to pad all samples to same length.
vectorize_layer = TextVectorization(
    standardize=custom_standardization,
    max_tokens=vocab_size,
    output_mode='int',
    output_sequence_length=sequence_length)

vectorize_layer.adapt(tweet_ds.batch(1024))

# Save the created vocabulary for reference.
inverse_vocab = vectorize_layer.get_vocabulary()
print(inverse_vocab[:20])

def vectorize_text(text):
  text = tf.expand_dims(text, -1)
  return tf.squeeze(vectorize_layer(text))

# Vectorize the data in text_ds.
tweet_vector_ds = tweet_ds.batch(1024).prefetch(AUTOTUNE).map(vectorize_layer).unbatch()
sequences = list(tweet_vector_ds.as_numpy_iterator())
print(len(sequences))

for seq in sequences[:5]:
  print(f"{seq} => {[inverse_vocab[i] for i in seq]}")

['', '[UNK]', 'the', 'to', 'and', 'of', 'you', 'coronavirus', 'a', 'in', 'covid19', 'for', 'we', 'this', 'can', 'is', 'on', 'our', 'if', 'have']
3536
[ 222    3   28    9  368  355   88  894    2  391   98  240  487    3
  422  107    4   50 1985  260 2586  193   25 8965    3 8315 7166    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0] => ['great', 'to', 'be', 'in', 'northern', 'ireland', 'today', 'seeing', 'the', 'incredible', 'work', 'being', 'done', 'to', 'tackle', 'covid', 'and', 'get', 'jabs', 'into', 'arms', '–', 'from', 'belfast', 'to', 'enniskillen', 'httpstcofq3zrvorge', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', 

In [ ]:
# Generates skip-gram pairs with negative sampling for a list of sequences
# (int-encoded sentences) based on window size, number of negative samples
# and vocabulary size.
def generate_training_data(sequences, window_size, num_ns, vocab_size, seed):
  # Elements of each training example are appended to these lists.
  targets, contexts, labels = [], [], []

  # Build the sampling table for vocab_size tokens.
  sampling_table = tf.keras.preprocessing.sequence.make_sampling_table(vocab_size)

  # Iterate over all sequences (sentences) in dataset.
  for sequence in tqdm.tqdm(sequences):

    # Generate positive skip-gram pairs for a sequence (sentence).
    positive_skip_grams, _ = tf.keras.preprocessing.sequence.skipgrams(
          sequence, 
          vocabulary_size=vocab_size,
          sampling_table=sampling_table,
          window_size=window_size,
          negative_samples=0)

    # Iterate over each positive skip-gram pair to produce training examples 
    # with positive context word and negative samples.
    for target_word, context_word in positive_skip_grams:
      context_class = tf.expand_dims(
          tf.constant([context_word], dtype="int64"), 1)
      negative_sampling_candidates, _, _ = tf.random.log_uniform_candidate_sampler(
          true_classes=context_class,
          num_true=1, 
          num_sampled=num_ns, 
          unique=True, 
          range_max=vocab_size, 
          seed=SEED, 
          name="negative_sampling")

      # Build context and label vectors (for one target word)
      negative_sampling_candidates = tf.expand_dims(
          negative_sampling_candidates, 1)

      context = tf.concat([context_class, negative_sampling_candidates], 0)
      label = tf.constant([1] + [0]*num_ns, dtype="int64")

      # Append each element from the training example to global lists.
      targets.append(target_word)
      contexts.append(context)
      labels.append(label)

  return targets, contexts, labels

In [ ]:
targets, contexts, labels = generate_training_data(
    sequences=sequences, 
    window_size=2, 
    num_ns=4, 
    vocab_size=vocab_size, 
    seed=SEED)
print(len(targets), len(contexts), len(labels))

100%|██████████| 3536/3536 [00:08<00:00, 422.62it/s]

57072 57072 57072


In [ ]:
BATCH_SIZE = 1024
BUFFER_SIZE = 10000
dataset = tf.data.Dataset.from_tensor_slices(((targets, contexts), labels))
dataset = dataset.shuffle(BUFFER_SIZE).batch(BATCH_SIZE, drop_remainder=True)
dataset = dataset.cache().prefetch(buffer_size=AUTOTUNE)
print(dataset)

<PrefetchDataset shapes: (((1024,), (1024, 5, 1)), (1024, 5)), types: ((tf.int32, tf.int64), tf.int64)>


In [ ]:
class Word2Vec(Model):
  def __init__(self, vocab_size, embedding_dim):
    super(Word2Vec, self).__init__()
    self.target_embedding = Embedding(vocab_size, 
                                      embedding_dim,
                                      input_length=1,
                                      name="w2v_embedding", )
    self.context_embedding = Embedding(vocab_size, 
                                       embedding_dim, 
                                       input_length=num_ns+1)
    self.dots = Dot(axes=(3,2))
    self.flatten = Flatten()

  def call(self, pair):
    target, context = pair
    we = self.target_embedding(target)
    ce = self.context_embedding(context)
    dots = self.dots([ce, we])
    return self.flatten(dots)

In [ ]:
def custom_loss(x_logit, y_true):
      return tf.nn.sigmoid_cross_entropy_with_logits(logits=x_logit, labels=y_true)

In [ ]:
embedding_dim = 128
num_ns = 4
word2vec = Word2Vec(vocab_size, embedding_dim)
word2vec.compile(optimizer='adam',
              loss=tf.keras.losses.CategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir="logs")

word2vec.fit(dataset, epochs=20, callbacks=[tensorboard_callback])

Epoch 1/20
55/55 [==============================] - 3s 33ms/step - loss: 1.6085 - accuracy: 0.2322
Epoch 2/20
55/55 [==============================] - 2s 30ms/step - loss: 1.5878 - accuracy: 0.7267
Epoch 3/20
55/55 [==============================] - 2s 30ms/step - loss: 1.5444 - accuracy: 0.8247
Epoch 4/20
55/55 [==============================] - 2s 30ms/step - loss: 1.4544 - accuracy: 0.8192
Epoch 5/20
55/55 [==============================] - 2s 31ms/step - loss: 1.3242 - accuracy: 0.8157
Epoch 6/20
55/55 [==============================] - 2s 30ms/step - loss: 1.1761 - accuracy: 0.8287
Epoch 7/20
55/55 [==============================] - 2s 30ms/step - loss: 1.0292 - accuracy: 0.8476
Epoch 8/20
55/55 [==============================] - 2s 29ms/step - loss: 0.8949 - accuracy: 0.8653
Epoch 9/20
55/55 [==============================] - 2s 29ms/step - loss: 0.7773 - accuracy: 0.8805
Epoch 10/20
55/55 [==============================] - 2s 29ms/step - loss: 0.6764 - accuracy: 0.8938
Epoch 11/

In [ ]:
import io
weights = word2vec.get_layer('w2v_embedding').get_weights()[0]
vocab = vectorize_layer.get_vocabulary()
out_v = io.open('vectors.tsv', 'w', encoding='utf-8')
out_m = io.open('metadata.tsv', 'w', encoding='utf-8')
out_m.write("header" + "\n")

for index, word in enumerate(vocab):
  if  index == 0: continue # skip 0, it's padding.
  vec = weights[index] 
  out_v.write('\t'.join([str(x) for x in vec]) + "\n")
  out_m.write(word + "\n")
out_v.close()
out_m.close()

try:
  from google.colab import files
  files.download('vectors.tsv')
  files.download('metadata.tsv')
except Exception as e:
  pass

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

TFIDF code start here


In [2]:
!git clone https://github.com/Data-Mining-2021/project.git

Cloning into 'project'...
remote: Enumerating objects: 194, done.
remote: Counting objects: 100% (194/194), done.
remote: Compressing objects: 100% (132/132), done.
remote: Total 194 (delta 81), reused 116 (delta 43), pack-reused 0
Receiving objects: 100% (194/194), 19.98 MiB | 10.27 MiB/s, done.
Resolving deltas: 100% (81/81), done.


In [11]:
import pandas as pd
from langdetect import detect
from sklearn.decomposition import TruncatedSVD
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer
from sklearn import metrics
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer
from langdetect import detect

europe_csv = pd.read_csv('/content/project/regions/Europe/europe_tweets.csv')

vectorizer = TfidfVectorizer(ngram_range=(2,2),stop_words={'english'})
X = vectorizer.fit_transform(europe_csv["Text"].values.astype('U'))
print(vectorizer.vocabulary_)
print(X.shape)
svd = TruncatedSVD(100)
normalizer = Normalizer(copy=False)
lsa = make_pipeline(svd, normalizer)

X = lsa.fit_transform(X)
print(X)


explained_variance = svd.explained_variance_ratio_.sum()
print("Explained variance of the SVD step: {}%".format(
    int(explained_variance * 100)))
print()

{'great to': 38393, 'to meet': 94469, 'meet bandq': 57807, 'bandq staff': 11751, 'staff in': 84134, 'in middlesbrough': 45961, 'middlesbrough to': 58395, 'to thank': 94921, 'thank them': 88532, 'them for': 91564, 'for their': 34488, 'their great': 91308, 'great work': 38404, 'work during': 104715, 'during the': 27977, 'the pandemic': 90357, 'pandemic today': 69019, 'today we': 95326, 'we increased': 101689, 'increased the': 46659, 'the nationallivingwage': 90253, 'nationallivingwage to': 60752, 'to 91': 93743, '91 an': 2127, 'an hour': 6125, 'hour which': 44020, 'which will': 102921, 'will provide': 103574, 'provide welcome': 73629, 'welcome boost': 102246, 'boost to': 14260, 'to families': 94176, 'families around': 32124, 'around the': 10012, 'the uk': 90944, 'uk as': 97170, 'as we': 10418, 'we buildbackbetter': 101599, 'buildbackbetter and': 15198, 'and fairer': 6851, 'fairer from': 32035, 'from the': 35723, 'our plan': 67865, 'plan for': 71024, 'for growth': 34115, 'growth sets': 38

In [14]:
import re

# https://stackoverflow.com/a/49146722/330558
def remove_emoji(string):
    emoji_pattern = re.compile("["
                               u"\U0001F600-\U0001F64F"  # emoticons
                               u"\U0001F300-\U0001F5FF"  # symbols & pictographs
                               u"\U0001F680-\U0001F6FF"  # transport & map symbols
                               u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                               u"\U00002500-\U00002BEF"  # chinese char
                               u"\U00002702-\U000027B0"
                               u"\U00002702-\U000027B0"
                               u"\U000024C2-\U0001F251"
                               u"\U0001f926-\U0001f937"
                               u"\U00010000-\U0010ffff"
                               u"\u2640-\u2642"
                               u"\u2600-\u2B55"
                               u"\u200d"
                               u"\u23cf"
                               u"\u23e9"
                               u"\u231a"
                               u"\ufe0f"  # dingbats
                               u"\u3030"
                               "]+", flags=re.UNICODE)
    return emoji_pattern.sub(r'', string)

european_csv = pd.read_csv('/content/project/regions/Europe/europe_tweets.csv')

european_english = []

# filter out non-english tweets - also checks for NaN and tweets only containing emojis
european_english = [content.encode('utf-8') for content in european_csv['Text'] 
                    if content == content and remove_emoji(content).strip() and detect(content) == 'en']



[b'Great to meet @BandQ staff in Middlesbrough to thank them for their great work during the pandemic.\n\nToday we increased the #NationalLivingWage to \xc2\xa38.91 an hour which will provide a welcome boost to families around the UK as we #BuildBackBetter and fairer from the pandemic. ', b"Our Plan for Growth sets our path to invest in infrastructure, skills and innovation so we can level up opportunity and prosperity across the country.\n\nThe government's open letter to businesses sets out how we can #BuildBackBetter ", b'No government can address the threat of pandemics alone \xe2\x80\x93 we must come together. \n\nMy joint article with other world leaders: ', b'The vaccine is our best route out of this pandemic and we must all do our part by taking the vaccine when it is offered to us.\n\nThank you Sir @LennyHenry for speaking up on this important issue. ', b'WATCH LIVE: an update on COVID-19 (29 March 2021) ', b'Today marks the next stage of our roadmap to cautiously ease restric

In [58]:
tweets = european_csv['Text'].tolist()
users = european_csv['Username'].tolist()
users_list = list(set(users))
vectorizer = TfidfVectorizer(ngram_range=(2,2),max_df = 0.8, stop_words={'english'})
users_tweet_vectorizer = {}

for user in users_list:
  users_tweet_vectorizer[user] = []

for index, tweet in enumerate(tweets):
  if tweet == tweet and remove_emoji(tweet).strip() and detect(tweet) == 'en':
    tweet = tweet.encode('utf-8')
    users_tweet_vectorizer[users[index]].append(tweet)


In [59]:
svd = TruncatedSVD(50)
normalizer = Normalizer(copy=False)
lsa = make_pipeline(svd, normalizer)

for user in users_tweet_vectorizer.keys():
  X = vectorizer.fit_transform(users_tweet_vectorizer[user])
  X = lsa.fit_transform(X)
  users_tweet_vectorizer[user] = X
  print(X.shape)

(2279, 50)
(933, 50)
(235, 50)
(4270, 50)
(100, 50)
(5343, 50)
(54, 50)


In [62]:
from sklearn.cluster import KMeans
import numpy as np

km = KMeans(n_clusters=5, init='k-means++', max_iter=100, n_init=1,
                verbose=False)

tweets = np.vstack(users_tweet_vectorizer.values())

tweets = np.array(tweets)
print(tweets.shape)
km.fit(tweets)
original_space_centroids = svd.inverse_transform(km.cluster_centers_)
order_centroids = original_space_centroids.argsort()[:, ::-1]
terms = vectorizer.get_feature_names()
for i in range(5):
  print("Cluster %d:" % i, end='')
  for ind in order_centroids[i, :10]:
    print(' %s' % terms[ind], end='')
  print()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:7: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  import sys


(13214, 50)
Cluster 0: with the together with the new president joebiden ready to governments and the pandemic of our and eu_commission the us
Cluster 1: overcome the response to exchange of of views the health health response on the the european to overcome the pandemic
Cluster 2: of the to the response to full support overcome the with president on the the joint let keep the pandemic
Cluster 3: of the the eu for the in the at the and the on the heart of the heart to the
Cluster 4: for the to working forward to president joebiden the us the next of our better future on the eu and
